<a href="https://colab.research.google.com/github/mikodham/CS470/blob/main/BaselineCode.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#SETUP

In [2]:
#REQUIREMENT, #don't forget to turn on gpu
!pip3 install nltk sklearn gensim xgboost keras
!pip install nltk==3.5


     |████████████████████████████████| 1.4MB 7.5MB/s 
  Created wheel for nltk: filename=nltk-3.5-cp37-none-any.whl size=1434694 sha256=4915d9b59465146cf246ac2689b96f3931e593537d6b8497c82793aebfdb1fe8
  Stored in directory: /root/.cache/pip/wheels/ae/8c/3f/b1fe0ba04555b08b57ab52ab7f86023639a526d8bc8d384306
Successfully built nltk
  Found existing installation: nltk 3.2.5
    Uninstalling nltk-3.2.5:
      Successfully uninstalled nltk-3.2.5


In [3]:
try:
    %tensorflow_version 2.x
except Exception:
    pass
import tensorflow as tf

import os
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import pprint
import argparse

In [4]:
import nltk
nltk.download('all')

[nltk_data] Downloading collection 'all'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/abc.zip.
[nltk_data]    | Downloading package alpino to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/alpino.zip.
[nltk_data]    | Downloading package biocreative_ppi to
[nltk_data]    |     /root/nltk_data...
[nltk_data]    |   Unzipping corpora/biocreative_ppi.zip.
[nltk_data]    | Downloading package brown to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/brown.zip.
[nltk_data]    | Downloading package brown_tei to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/brown_tei.zip.
[nltk_data]    | Downloading package cess_cat to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/cess_cat.zip.
[nltk_data]    | Downloading package cess_esp to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/cess_esp.zip.
[nltk_data]    | Downloading package chat80 to /root/nltk_data...
[nltk_data]    |   Unzipp

True

#PREPROCESSING
1. Download Dataset
2. Load Dataset
3. Pre-process sentence into features



##1. Load Dataset - REDDIT

In [5]:
# 1st option, upload on ur gdrive
# from google.colab import files
# files.upload()
# 2nd option, just drag the folder from your folder to drive/content/

# 3rd option, git clone
!pwd
!rm -rf intellibots_spring21 # FOR UPDATING DATASET DO NOT RUN THIS LINE
!git clone https://github.com/mikodham/intellibots_spring21/


/content
Cloning into 'intellibots_spring21'...
remote: Enumerating objects: 120, done.
remote: Counting objects: 100% (120/120), done.
remote: Compressing objects: 100% (109/109), done.
remote: Total 120 (delta 52), reused 40 (delta 9), pack-reused 0
Receiving objects: 100% (120/120), 9.63 MiB | 15.95 MiB/s, done.
Resolving deltas: 100% (52/52), done.


###Cleaning The Dataset and Data Extraction

EXTRACT DATASET FROM ZENODO

In [6]:
# FILENAME = "master_data.csv"
# FILEDIR = os.path.join(os.getcwd(), "Dataset", FILENAME)
# # print(FILEDIR)
master_df = pd.DataFrame()

file_urls = [
    "https://zenodo.org/record/4543776/files/Redditors_and_posts_batch_1.xlsx", # 757 posts
    "https://zenodo.org/record/4543776/files/Redditors_and_posts_batch_2.xlsx", # 934 posts
    "https://zenodo.org/record/4543776/files/Redditors_and_posts_batch_3.xlsx", # 837 posts
    "https://zenodo.org/record/4543776/files/Redditors_and_posts_batch_4.xlsx", # 983 posts 
    "https://zenodo.org/record/4543776/files/Redditors_and_posts_batch_5.xlsx", # 761 posts
]

for file_url in file_urls:
    dfs = pd.read_excel(file_url,sheet_name=None,usecols="A:B") # 1 dataframe for each sheet within an excel file
    df = pd.concat(dfs,ignore_index=True) # merging the dataframes for each sheet
    master_df = pd.concat([master_df,df],ignore_index=True) # merging the dataframes for each file

df_negatives_zenodo = master_df[master_df['Suicide Risk'].isin(['supportive','uninformative'])]
df_negatives_zenodo.reset_index(drop=True,inplace=True)
print(df_negatives_zenodo.head(10))

df_positives_zenodo = master_df[master_df['Suicide Risk'].isin(['attempt','behavior','indicator','ideation'])]
df_positives_zenodo.reset_index(drop=True,inplace=True)
print(df_positives_zenodo.head(10))


print(len(df_negatives_zenodo.index),len(df_positives_zenodo.index))



                                         Reddit Post Suicide Risk
0  Thank you very much for the picture. I printed...   supportive
1  'Try 7 years and a kid bub. It sucks when thin...   supportive
2  'now youre putting the pussy on a pedestal hah...   supportive
3  'Dont use that book as your basis of your unde...   supportive
4  Its not a viable option, and youll be leaving ...   supportive
5  It can be hard to appreciate the notion that y...   supportive
6  'The voice is just a voice. People can praise ...   supportive
7  'You indeed sound Tired bipolar. Bipolar is wh...   supportive
8  'You will always come back so much stronger af...   supportive
9  'You should never allow yourself the space to ...   supportive
                                         Reddit Post Suicide Risk
0  My girlfriend of 7 years recently broke up wit...     ideation
1  'I know how you feel man. My ex and I were tog...    indicator
2  'Thats good to know. Im only familiar with vic...    indicator
3  'I thin

EXTRACT DATA FROM KAGGLE DATASET

In [7]:
#DATA_FOLDER = '/content/intellibots_spring21/Dataset/'

df_reddit = pd.DataFrame()
path = os.path.join(os.getcwd(), "intellibots_spring21", "Dataset", "reddit_mini.csv") # path = "./Dataset/reddit_mini.csv"
df_reddit = pd.read_csv(path,usecols=[1,2]) 

df_negatives_reddit = df_reddit[df_reddit['class'].isin(['non-suicide'])]
df_negatives_reddit.reset_index(drop=True,inplace=True)
print(df_negatives_reddit.head(10))

df_positives_reddit = df_reddit[df_reddit['class'].isin(['suicide'])]
df_positives_reddit.reset_index(drop=True,inplace=True)
print(df_positives_reddit.head(10))

print(len(df_negatives_reddit.index),len(df_positives_reddit.index))

                                                text        class
0  You're at a party and they start passing aroun...  non-suicide
1  How to dodge a thot? (For real) 1. Masturbate ...  non-suicide
2  Does anyone want to talk? I'm F18, in quaranti...  non-suicide
3  Someone pls help me rq? I need to write a summ...  non-suicide
4  Ok, you know what? I'm taking a picture of eve...  non-suicide
5  I need someone to talk to I am sad, i want som...  non-suicide
6  the constant struggle to be the pure wholesome...  non-suicide
7  Good morning everyone 😁😁😁 What are your plans ...  non-suicide
8  I love my parents! I've been saving for a Nint...  non-suicide
9  Diamond Certified Singer The Weeknd - Save You...  non-suicide
                                                text    class
0  Failed Attempt #1Last night I had a couple fri...  suicide
1  I feel so fucking aloneI just want someone to ...  suicide
2  I’m stuck here and I’m so scaredDisclaimer thi...  suicide
3  Not the psychosisFor th

In [8]:
#Learn How to iterate those
# df_negatives_reddit.iloc[1000] #text:[0], class:[1]
df_positives_zenodo #reddit post and suicide risk
# df_negatives_zenodo.iloc[1251]
# df_positives_reddit
# df_negatives_reddit
# df_negatives_reddit['class']

Reddit Post Suicide Risk
0    My girlfriend of 7 years recently broke up wit...     ideation
1    'I know how you feel man. My ex and I were tog...    indicator
2    'Thats good to know. Im only familiar with vic...    indicator
3    'I think one of the hardest things about this ...    indicator
4    'Thank you.  I actually am not on any medicati...     ideation
..                                                 ...          ...
773  'Yeah I know. Im not even really sure how I fe...    indicator
774  this is a sad story for sure and I am telling ...    indicator
775  'Well, You know you can always come speak to u...    indicator
776  'You arent alone. You know you can always come...    indicator
777  'I am struggling with something very similar t...    indicator

[778 rows x 2 columns]

In [9]:
# TODO: Find the right data structure to match tensorflow dataset, so that the train and test data
# will be trainable

# Features Extraction

In [10]:
def POSTAG():
  # Input example
  """
  array([[(sentence, label), (sentence, label), (sentence, label), ..., (sentence, label)],
        [(sentence, label), (sentence, label), (sentence, label), ..., (sentence, label)]])
  """
  # POS_TAG
  # https://datascience.stackexchange.com/questions/16379/word-embedding-word2vec-for-pos-tagging
  init_input = [
                [("hello i like cheese!", 1), ("never mind i hate cheese!", 2)],
                [("cheese is not bad", 1), ("it's really bad", 1)]
              ]
  
  # into form [[(["hello","i","like","cheese","!"], 1)]]
  processed_input = []*len(init_input)
  for i in range(len(init_input)):
    for data_points in init_input[i]:
      # print(data_points)
      processed_input.append(nltk.tokenize.word_tokenize(data_points[0]))
  print(processed_input)

  tags = [nltk.pos_tag(text) for text in processed_input]
  print(tags)
  word_tags = []
  print(word_tags)

  for i in range(len(tags)):
    # print(tags[i])
    just_tags = [tag for (word,tag) in tags[i]]
    # print(just_tags)
    word_tags.append(just_tags)
  # print(word_tags)

  import gensim, logging
  logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
 # train word2vec on the two sentences
  model_tag = gensim.models.Word2Vec(word_tags, min_count=1) # prunes the internal dictionary
  return model_tag

In [11]:
def Word2Vec():
  import nltk
  input = [[("hello i like cheese!", 1), ("never mind i hate cheese!", 2)],
          [("cheese is not bad", 1), ("it's really bad", 1)]
  ]

  # into form [[(["hello","i","like","cheese","!"], 1)]]
  # print(processed_input)
  # import modules & set up logging
  import gensim, logging
  logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
  # train word2vec on the two sentences
  model_word = gensim.models.Word2Vec(processed_input, min_count=1) # prunes the internal dictionary
  return model_word

In [12]:
def TF_IDF():
  from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
  import pandas as pd

  input_sentences = [] # list of all sentences in the corpus
  for feature in init_input:
    for (word, tag) in feature:
      input_sentences.append(word)
  print(input_sentences)

  def tf_idf(data): # data should be list of strings
    count_vect = CountVectorizer(ngram_range=(1, 1), max_features=50) # get all stopwords
    data_counts = count_vect.fit_transform(data)
    tfidf_transformer = TfidfTransformer()
    data_train_tfidf = tfidf_transformer.fit_transform(data_counts)
    df_tfidf = pd.DataFrame(data_train_tfidf.todense())
    return df_tfidf

  tf_idf_r = tf_idf(input_sentences)
  print(tf_idf_r)
  return tf_idf(tf_idf_r)

In [13]:
def BOW_TFIDF(input_sentences):
  import nltk
  from nltk.corpus import stopwords
  from nltk.probability import FreqDist
  import numpy
  import math
  

  #SOME DATA ARE NOT CLEAN, Nan is found, non-string, Need to remove them in Preprocessed part
  
  # Bag of words
  # tokenizes sentences
  def word_extraction(sentence):
    # ignore = stopwords.words('english')
    tweet_tokenizer = nltk.TweetTokenizer()
    words = tweet_tokenizer.tokenize(sentence)
    cleaned_text = [w.lower() for w in words]
    return cleaned_text
  # word_extraction("list of all sentences hello in the corpus!")

  # goes through all the sentences and adds the words to one list
  def create_vocab(sentences):
    words = []
    c=0
    for sentence in sentences:
      w = word_extraction(sentence)
      words.extend(w)
    print("DONE EXTRACT")
    words = sorted(list(set(words)))
    return words
  # print(create_vocab(input_sentences))

  # print("all_Sentences: ", input_sentences)
  def BOW(all_sentences):
    vocab = create_vocab(all_sentences)
    # print("VOCAB: ", vocab)
    sentence_tokens = list(map(lambda x: word_extraction(x), all_sentences))
    sentence_vectors = [] 
    # for each sentence, find the frequency of words in the vocab
    for sentence in sentence_tokens:
      # print("sentence: ", sentence)
      fdist = FreqDist(sentence)
      vector = []
      for word in vocab:
        vector.append(fdist[word])
      sentence_vectors.append(vector)
    return sentence_vectors

  def TF_IDF(all_sentences):
    vocab = create_vocab(all_sentences)
    print("VOCAB: ", vocab)
    print("vOCAB size", len(vocab))
    sentence_tokens = list(map(lambda x: word_extraction(x), all_sentences))
    all_fdist = list(map(lambda x: FreqDist(x), sentence_tokens))
    sentence_vectors = []
    for sentence in sentence_tokens:
      vector = []
      for word in vocab:
        # TF
        sentence_fdist = FreqDist(sentence) # for each sentence
        tf = sentence_fdist[word] / len(sentence)
        # Idf
        sentence_with_word = 0
        for fdist in all_fdist:
          if fdist[word] >= 1:
            sentence_with_word += 1
        idf = math.log(len(sentence) / sentence_with_word)
        vector.append(tf*idf)
      sentence_vectors.append(vector)
    return sentence_vectors, len(vocab)
    
  bow_features = BOW(input_sentences)
  print("BOW: ", bow_features)
  print("LEN BOW:", len(bow_features))
  tfidf_features, vocab_size = TF_IDF(input_sentences)
  print("TF-IDF: ",tfidf_features )
  print("LEN TF_IDF:", len(tfidf_features))
  return vocab_size, bow_features, tfidf_features

In [14]:
def LDA(input_sentences):
  from sklearn.decomposition import LatentDirichletAllocation
  from sklearn.datasets import make_multilabel_classification
  from sklearn.feature_extraction.text import CountVectorizer
  # This produces a feature matrix of token counts, similar to what
  # CountVectorizer would produce on text.
  def lda2vec(all_senteneces):
    vocab = create_vocab(all_senteneces)
    vectorizer = CountVectorizer(all_senteneces,tokenizer=word_extraction)
    X = vectorizer.fit_transform(all_senteneces)
    print(vectorizer.vocabulary_) # topics
    lda = LatentDirichletAllocation(n_components=len(vocab),random_state=0)
    lda.fit(X)

    # get topics for some given samples:
    print("Samples Points: ", lda.transform(X[-2:]))
    return lda
  
  print(lda2vec(input_sentences))
  return lda2vec(input_sentences)

# Extract from Zenodo

In [15]:
# list(df_negatives_zenodo['Reddit Post'])
# ONLY NEGATIVES DATA SO FAR
print(list(df_negatives_zenodo['Reddit Post'])[1251])

# def get_zenodo(n_train, n_valid, n_pred): 
n_train,  n_pred = 500, 700
'''
  zenodo: Negative 1609 ['supportive','uninformative']
          Positive 778 ['attempt','behavior','indicator','ideation']
  Index of Extraction: n_train < n_pred
  Maximum n_pred is 750
  Return Dataset for 6 classifications, balanced data between positive and negative
'''
import random
if n_pred > 750: raise AssertionError("n_pred exceeds")
if (n_train < n_pred) is False: raise AssertionError("Input Order Error")
positive_sents = list(df_positives_zenodo['Reddit Post'][:n_pred])
# print(type(positive_sents))
negative_sents = list(df_negatives_zenodo['Reddit Post'][:n_pred])
extracted_sentences = positive_sents + negative_sents # list of all sentences in the corpus
extracted_sentences = [str(sent) for sent in extracted_sentences] 

extracted_labels = list(df_positives_zenodo['Suicide Risk'][:n_pred])
extracted_labels += list(df_negatives_zenodo['Suicide Risk'][:n_pred])
labels = ['supportive','uninformative','attempt','behavior','indicator','ideation']
extracted_labels = [labels.index(each) for each in extracted_labels]

# Shuffle
seed = random.random()
random.seed(seed) 
random.shuffle(extracted_sentences)
random.seed(seed)
random.shuffle(extracted_labels)
# # Shuffle
# indices = np.arange(extracted_sentences.shape[0])
# np.random.shuffle(indices)
# extracted_sentences = extracted_sentences[indices]
# extracted_labels = extracted_labels[indices]

# TRAIN
train_sentences = extracted_sentences[:n_train]
train_labels = extracted_labels[:n_train]

# TEST
test_sentences = extracted_sentences[n_train:n_pred]
test_labels = extracted_labels[n_train:n_pred]
# print(corY_labels)
# Should I convert into digits of classes?

nan


In [16]:
extracted_sentences[:5]


['You may feel hopeless today but it is not too late to change your path, your velocity. Your situation is common in many places in the world. You may feel as though youve out grown any opportunity but that is absolutely not the case. http://www.ted.com/talks/amy_cuddy_your_body_language_shapes_who_you_are?language=enThis Ted Talk (short video) absolutely changed the way I live, as silly as it sounds. I dont know whats possessing me to share it with you, but I feel Hyperactive behavior I have a lot in common as an Respiratory Distress Syndrome, Adult struggling to have a career, and build myself a life. And this talk really helped ME overcome the overwhelming sense of dread and fear I have walking into a job interview, or just walking out of the front door.I think something as small as a part time job could lift you up. You may not have $30,000 in a bank account overnight, but right now my friend, you have no where to go but up.What youre feeling today though, is not what youll always 

In [17]:
extracted_labels[:5]

[0, 0, 0, 0, 0]

In [18]:
vocab_size, bow_features, tfidf_features = BOW_TFIDF(train_sentences)
#Warning: This takes a long Time!

DONE EXTRACT


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



DONE EXTRACT
VOCAB:  ['!', '"', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '. ..', '. ...', '..', '...', '/', '0,1', '0,5-', '02', '1', '1/2', '10', '10-15', '100', '11', '1130', '13', '14', '15', '16', '17', '17.and', '1781.5', '18', '1839', '19', '1st', '2', '2-3', '20', '2000', '2008', '20mg', '20s', '21', '22', '24', '25', '25000', '27', '28', '29th', '2nd', '3', '30', '30,000', '300', '3000', '300mg', '35', '350', '357', '4', '4-6', '4.0', '4/20', '40', '45', '5', '5-10', '50', '50.dont', '5mg', '5th', '6', '60', '600k', '7', '700', '70s', '72', '8', '8.03', '80', '8th', '9', '900', '911', '95-99', '99', ':', ':(', ':)', ':-)', ':/', ':\\', ':|', ';', ';d', '<', '<3', '=)', '>', '?', '\\', ']', 'a', 'abandoned', 'ability', 'able', 'abnormal', 'about', 'above', 'absences', 'absolute', 'absolutely', 'absurdly', 'abundantly', 'abuse', 'abuse.last', 'abused', 'abusive', 'abyss', 'academic', 'academically', 'acceleration', 'accent', 'accept', 'acceptance', 'accepted', 'acce

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [19]:
print(tfidf_features[200])

[0.0, 0.0, 0.0, 0.0, 0.0, -0.004113075873693758, 0.0, 0.0, 0.0, 0.0, -0.03601559291485872, 0.0, -0.03681478791357114, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -0.021026632226893945, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

#Extract from Kaggle

In [20]:
# list(df_negatives_zenodo['Reddit Post'])
# ONLY NEGATIVES DATA SO FAR
print(list(df_negatives_reddit['text'])[1251])

# def get_zenodo(n_train, n_valid, n_pred): 
n_train,  n_pred = 100, 150
'''
  zenodo: Negative 1609 ['supportive','uninformative']
          Positive 778 ['attempt','behavior','indicator','ideation']
  Index of Extraction: n_train < n_pred
  Maximum n_pred is 750
  Return Dataset for 6 classifications, balanced data between positive and negative
'''
import random
if n_pred > 10000: raise AssertionError("n_pred exceeds")
if (n_train < n_pred) is False: raise AssertionError("Input Order Error")
positive_sents = list(df_positives_reddit['text'][:n_pred])
# print(type(positive_sents))
negative_sents = list(df_negatives_reddit['text'][:n_pred])
extracted_sentences = positive_sents + negative_sents # list of all sentences in the corpus
extracted_sentences = [str(sent) for sent in extracted_sentences] 

extracted_labels = list(df_positives_reddit['class'][:n_pred])
extracted_labels += list(df_negatives_reddit['class'][:n_pred])
extracted_labels = [each=='suicide' for each in extracted_labels]

# Shuffle
seed = random.random()
random.seed(seed) 
random.shuffle(extracted_sentences)
random.seed(seed)
random.shuffle(extracted_labels)
# # Shuffle
# indices = np.arange(extracted_sentences.shape[0])
# np.random.shuffle(indices)
# extracted_sentences = extracted_sentences[indices]
# extracted_labels = extracted_labels[indices]

# TRAIN
train_sentences_kaggle = extracted_sentences[:n_train]
train_labels_kaggle = extracted_labels[:n_train]

# TEST
test_sentences_kaggle = extracted_sentences[n_train:n_pred]
test_labels_kaggle = extracted_labels[n_train:n_pred]
# print(corY_labels)
# Should I convert into digits of classes?

I’m starting to dread the night Every night for the past week idk why but my mind has started to go to a dark place. I just feel so alone and like I’m wasting my life. But during the day I feel fine like right now I’m great I’m just dreading tonight.


In [21]:
vocab_size_kaggle, bow_features_kaggle, tfidf_features_kaggle = BOW_TFIDF(train_sentences_kaggle)

DONE EXTRACT
BOW:  [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0

#RNN

In [22]:
def arg_rnn():
    parser = argparse.ArgumentParser()
    parser.add_argument('--max_seq_len', type=int, default=1000, help="max length of sequences")
    parser.add_argument('--max_num_words', type=int, default=20000, help="max number of words")
    parser.add_argument('-d', '--embedding_dim', type=int, default=300, help="embedding dimension")
    parser.add_argument('--rnn_units', type=int, default=128, help="units of RNN")
    parser.add_argument('--dropout_rate', type=float, default=0.1, help='dropout rate')
    parser.add_argument('--dense_units', type=int, default=32, help="units of Dense layer")
    parser.add_argument('--embedding_type', type=str, default='word2vec', help="the type of word embedding")
    parser.add_argument('--valid_split', type=float, default=0.1, help="ratio of validation split")
    parser.add_argument('-act', '--activation', type=str, default='relu', help="type of activation function")
    parser.add_argument('--patience', type=int, default=10, help="number of epochs with no improvement after which training will be stopped")
    parser.add_argument('--batch_size', type=int, default=64, help="batch size")
    parser.add_argument('--epochs', type=int ,default=10, help="training epochs")
    # args = parser.parse_args()
    args, unknown = parser.parse_known_args()
    return args

In [23]:
def build_RNN(args):
    model = tf.keras.Sequential([
      tf.keras.layers.Embedding(vocab_size, args.embedding_dim), 
      tf.keras.layers.SimpleRNN(128, return_sequences=True),
      tf.keras.layers.GlobalMaxPool1D(),
      tf.keras.layers.Dropout(args.dropout_rate),
      tf.keras.layers.BatchNormalization(),
      tf.keras.layers.Dense(args.dense_units, activation="relu"),
      tf.keras.layers.Dropout(args.dropout_rate),
      tf.keras.layers.BatchNormalization(),
      tf.keras.layers.Dense(1, activation="sigmoid")
    ])
    model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [20]:
# def build_RNN(args):
#     # TODO: Tim, please modify this part use tf.keras instead of keras.model
#     # model = tf.keras.Sequential([
#     #     tf.keras.layers.Dense(16,activation='relu',input_shape=(NUM_WORDS,)),
#     # ])
#     # inp1 = tf.keras.layers.Input(shape=(args.max_seq_len, ))
#     # inp2 = tf.keras.layers.Input(shape=(args.max_seq_len, ))
#     model = tf.keras.Sequential([
#       tf.keras.layers.Embedding(vocab_size, args.embedding_dim), 
#       # x2 = tf.keras.layers.Embedding(args.max_num_words, args.embedding_dim)(inp2)
#       tf.keras.layers.SimpleRNN(128, return_sequences=True),
#       # x2 = tf.keras.layers.SimpleRNN(args.rnn_units, return_sequences=True)(x2)
#       # x = tf.keras.layers.concatenate([x1, x2])
#       tf.keras.layers.GlobalMaxPool1D(),
#       tf.keras.layers.Dropout(args.dropout_rate),
#       tf.keras.layers.BatchNormalization(),
#       tf.keras.layers.Dense(args.dense_units, activation="relu"),
#       tf.keras.layers.Dropout(args.dropout_rate),
#       tf.keras.layers.BatchNormalization(),
#       tf.keras.layers.Dense(1, activation="sigmoid")
#       # model = tf.keras.models.Model(inputs=[inp1, inp2], outputs=x)
#     ])
#     model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
#     return model

In [24]:
RNN_arg = arg_rnn()
RNN_model = build_RNN(RNN_arg)
X1_train = np.asarray(tfidf_features)
X2_train = np.asarray(train_labels)
RNN_model.fit(X1_train, X2_train, validation_split=0.1, epochs=40)
print("DONE")
# early = EarlyStopping(monitor="val_loss", mode="min", patience=20)
# model.fit([X1_train, X2_train], y_train, batch_size=args_rnn.batch_size, epochs=args_rnn.epochs,
#           validation_split=0.1, callbacks=[early])

# BUG FOUND IN USING TF-IDF

Epoch 1/40
 1/15 [=>............................] - ETA: 1:58 - loss: nan - accuracy: 0.3438

InvalidArgumentError: ignored

In [ ]:
# PLOT EVALUATION
acc = history.history['accuracy']
val_acc = history.history['val_accuracy']

loss = history.history['loss']
val_loss = history.history['val_loss']

plt.figure(figsize=(8, 8))
plt.subplot(2, 1, 1)
plt.plot(acc, label='Training Accuracy')
# plt.plot(val_acc, label='Validation Accuracy')
plt.legend(loc='lower right')
plt.ylabel('Accuracy')
plt.ylim([min(plt.ylim()),1])
plt.title('Training Accuracy')

plt.subplot(2, 1, 2)
plt.plot(loss, label='Training Loss')
# plt.plot(val_loss, label='Validation Loss')
plt.legend(loc='upper right')
plt.ylabel('Cross Entropy')
plt.ylim([0,1.0])
plt.title('Training Loss')
plt.xlabel('epoch')
plt.show()

In [22]:
# Evaluation Part
v, bowtest_features, tfidftest_features = BOW_TFIDF(test_sentences)


DONE EXTRACT
BOW:  [[0, 0, 0, 0, 1, 0, 0, 0, 0, 2, 0, 0, 7, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [23]:
test_loss, test_accuracy = RNN_model.evaluate(np.asarray(bowtest_features), np.asarray(test_labels))

print(f'Test accuracy: {test_accuracy:.4f}')
print(f'Test loss: {test_loss:.4f}')

7/7 [==============================] - 2s 204ms/step - loss: -0.6683 - accuracy: 0.0550
Test accuracy: 0.0550
Test loss: -0.6683


#LET'S USE THE MODEL AS A BASELINE FOR SUICIDAL CLASSIFICARTION

In [25]:
RNN_model.trainable = False
MNT_model = tf.keras.Sequential([
    RNN_model,
    tf.keras.layers.GlobalAveragePooling1D(),
    tf.keras.layers.Dense(1,activation='sigmoid')
])

MNT_model.compile(
    optimizer = 'RMSprop',
    loss = 'binary_crossentropy',
    metrics = ['accuracy']
)


ValueError: ignored

In [ ]:
history = MNT_model.fit(
    np.asarray(bow_features_kaggle),
    np.asarray(train_labels_kaggle)
    validation_split=0.1
    epochs=10
)


In [ ]:
# Evaluation Part
v, bowtestKaggle_features, tfidftestKaggle_features = BOW_TFIDF(test_sentences_kaggle)


In [ ]:
test_loss, test_accuracy = MNT_model.evaluate(np.asarray(bowtestKaggle_features), np.asarray(test_labels_kaggle))

print(f'Test accuracy: {test_accuracy:.4f}')
print(f'Test loss: {test_loss:.4f}')

#LSTM

In [ ]:
import numpy as np
from tqdm import tqdm
from tabulate import tabulate
from sklearn.model_selection import KFold
from keras.models import Model
from keras.layers import Dense, Embedding, Input
from keras.layers import LSTM, GlobalMaxPool1D, Dropout, BatchNormalization
from keras.preprocessing import text, sequence
from keras.callbacks import EarlyStopping

In [ ]:
def build_LSTM(args):
    # From XiongJi's Github
    inp = Input(shape=(args.max_seq_len, ))
    # x = Embedding(input_dim=args.max_num_words, output_dim=args.embedding_dim)(inp)
    # x = LSTM(units=args.lstm_units, activation='tanh', dropout=args.dropout_rate, return_sequences=True)(x)
    # x = GlobalMaxPool1D()(x)
    # x = Dropout(args.dropout_rate)(x)
    # x = BatchNormalization()(x)
    # x = Dense(args.dense_units, activation="relu")(x)
    # x = Dropout(args.dropout_rate)(x)
    # x = BatchNormalization()(x)
    # x = Dense(1, activation="sigmoid")(x)

    # TODO: Nabila, please modify this part use tf.keras instead of keras.model
    # model = tf.keras.Sequential([
    #     tf.keras.layers.Dense(16,activation='relu',input_shape=(NUM_WORDS,)),
    # ])

    model = Model(inputs=inp, outputs=x)

    model.compile(
        loss='binary_crossentropy', 
        # OR 'sparse_categorical_crossentropy' for multiclassifcation
        optimizer='adam', 
        # OR 'RMSprop'
        metrics=['accuracy'])
    return model


# RUN For Reddit

In [ ]:
# TODO: Find the right shuffling method and training method
'''
title_train = X1[train_ix]
title_test = X1[test_ix]
usertext_train = X2[train_ix]
usertext_test = X2[test_ix]
y_train = y[train_ix]
y_test = y[test_ix]

tokenizer = text.Tokenizer(num_words=args_rnn.max_num_words)
tokenizer.fit_on_texts(list(title_train)+list(usertext_train))
tokenized_title_train = tokenizer.texts_to_sequences(title_train)
tokenized_title_test = tokenizer.texts_to_sequences(title_test)
tokenized_usertext_train = tokenizer.texts_to_sequences(usertext_train)
tokenized_usertext_test = tokenizer.texts_to_sequences(usertext_test)
X1_train = sequence.pad_sequences(tokenized_title_train, maxlen=args_rnn.max_seq_len, dtype='float64')
X1_test = sequence.pad_sequences(tokenized_title_test, maxlen=args_rnn.max_seq_len, dtype='float64')
X2_train = sequence.pad_sequences(tokenized_usertext_train, maxlen=args_rnn.max_seq_len, dtype='float64')
X2_test = sequence.pad_sequences(tokenized_usertext_test, maxlen=args_rnn.max_seq_len, dtype='float64')

# train model and predict
model = build_RNN(args=args_rnn)
early = EarlyStopping(monitor="val_loss", mode="min", patience=20)
model.fit([X1_train, X2_train], y_train, batch_size=args_rnn.batch_size, epochs=args_rnn.epochs,
          validation_split=0.1, callbacks=[early])

y_pred = model.predict([X1_test, X2_test]).reshape(y_test.shape)
'''